## Ansible management LXC setup.

Pickup one of the Ansible management containers, lxcans01 -- lxcans05. It would be preferable if you match 
 the number with that of your lxc container.
 
The user name and password are the same as on your lxc.

Install ansible:
```bash
sudo apt install ansible
```

Work as user hostadm in all the steps below.

On lxcans# container, download Ansible.tgz with the ceph related playbooks:
```bash
wget https://linuxcourse.rutgers.edu/Winlab_Internship_2023/html/files/Ansible.tgz
```

Untar the archive:
```bash
tar -zxvf Ansible.tgz
cd Ansible
```


### Get your node reimaged through FOG

Schedule FOG for image deployment on your node.

Reboot the node to boot from network.

### Passwordless SSH login setup to your node and LXC container.

Change the hosts assignment in `hosts= ...` line in script ```ssh_hostadm_key.sh.```
Put your lxc and your node name there.

Run the script:
```bash
./ssh_hostadm_key.sh
``` 

Give the password for the node access by hostadm.

This should set passwordless ssh access to your node and lxc container. Try ssh to them from your lxcans contasiner to verify you can login without password.

### Modify the inventory file, hosts.ini

Put the correct node name in hosts.ini



### Passwordless sudo

Run the ansible playbook to setup passwordless sudo on the node:
```bash
ansible-playbook sudoers.yml --ask-become-pass
```
Provide the login password for hostadm to the node.

This should setup passwordless sudo for hostadm on the node.
SSH to the node and check it.

### Fix the hostname on the node.

Run the ansible playbook for fixing the hostname:
```bash
ansible-playbook fix_hostname_tasks.yml
```

SSH to the node to check if the hostname is fixed.

### Deploy Ceph on the node.

Run the playbook:
```bash
ansible-playbook ceph_one_node.yml
```

If it fails at the Dashboard setup, re-run it again.


### Steps to create Ansible playbook for CephFS mounting

- Add your lxc container to the inventory file, hosts.ini
  For example
```{addmonition} hosts.ini block:
    [ceph_mounts]
    lxc06
```
- In directory Ansible, create new file ```mount_ceph.yml``` with a play for ceph_mounts and role mount_ceph:

```{admonition} mount_ceph.yml:
    ---
    - name: Mount CephFS on the clients
      hosts: ceph_mounts

      roles:
        - mount_ceph
```

- Create directory tree under Ansible:
   ```roles/mount_ceph/tasks```, ```roles/mount_ceph/files```
   
- In directory roles/mount_ceph/tasks, create file main.yml, and start composing the tasks in main.yml

- You'll need to base the tasks on the following modules:

    - ansible.builtin.shell
    - ansible.builtin.fetch
    - ansible.builtin.copy
    
- File ```ceph.conf``` needs to be fetched from the node. Then it needs to be copied onto your lxc container.

- Similarly, you'll need to copy the key.

- Check your playbook for syntactic errors:
```bash
ansible-playbook  mount_ceph.yml --syntax-check
```
- If no errors show up, run the playbook:
```bash
ansible-playbook mount_ceph.yml
```